# Interactive visualisaztion
## Data Loading

In [15]:
import pandas as pd
import geopandas as gpd
data_path = 'data/statistical-gis-boundaries-london/ESRI2/'
gdf_lsoa = gpd.read_file(data_path + 'LSOA_2011_London_gen_MHW.shp' )[['LSOA11CD','geometry']]\
                .rename(columns={'LSOA11CD':'area_id'})
gdf_msoa = gpd.read_file(data_path + 'MSOA_2011_London_gen_MHW.shp' )[['MSOA11CD','geometry']]\
                .rename(columns={'MSOA11CD':'area_id'})
gdf_ward = gpd.read_file(data_path + 'London_Ward_CityMerged.shp')[['GSS_CODE','geometry']]\
               .rename(columns={'GSS_CODE':'area_id'})
gdf_borough = gpd.read_file(data_path + 'London_Borough_Excluding_MHW.shp' )[['GSS_CODE','geometry']]\
               .rename(columns={'GSS_CODE':'area_id'})
gdf = pd.concat([gdf_lsoa,gdf_msoa,gdf_ward,gdf_borough])
gdf.head()

area_id                                           geometry
0  E01000001  POLYGON ((532105.092 182011.230, 532162.491 18...
1  E01000002  POLYGON ((532746.813 181786.891, 532671.688 18...
2  E01000003  POLYGON ((532135.145 182198.119, 532158.250 18...
3  E01000005  POLYGON ((533807.946 180767.770, 533649.063 18...
4  E01000006  POLYGON ((545122.049 184314.931, 545271.917 18...

In [16]:
df = pd.read_csv('data/tesco.csv')
df.head()

area_id       fat  saturate      sugar   protein       carb     fibre  \
0  E09000001  8.472985  3.361599   9.278065  5.253333  15.779639  1.619850   
1  E09000002  9.209959  3.596834  10.793244  5.193872  19.784988  1.590335   
2  E09000003  8.594464  3.407353   9.530548  5.129627  17.025950  1.638639   
3  E09000004  9.119180  3.466346  10.941085  5.304496  19.997105  1.657118   
4  E09000005  8.962466  3.559913  10.148610  5.132915  18.726476  1.585978   

   energy_tot  h_nutrients_calories month agg_level  
0  165.851751              1.618208   yea   borough  
1  187.174390              1.545272   yea   borough  
2  170.655504              1.581507   yea   borough  
3  187.754791              1.551703   yea   borough  
4  180.510586              1.555736   yea   borough

In [33]:

merged_tot = gdf.merge(df, on='area_id', how = 'left')
#Replace NaN values to string 'No data'.
merged_tot.fillna('No data', inplace = True)
merged  = merged_tot.query("agg_level=='lsoa' and month=='Sep'")
feature = merged.fibre
merged

area_id                                           geometry      fat  \
10     E01000001  POLYGON ((532105.092 182011.230, 532162.491 18...  8.89254   
23     E01000002  POLYGON ((532746.813 181786.891, 532671.688 18...  7.27065   
36     E01000003  POLYGON ((532135.145 182198.119, 532158.250 18...  8.40703   
49     E01000005  POLYGON ((533807.946 180767.770, 533649.063 18...  8.29907   
62     E01000006  POLYGON ((545122.049 184314.931, 545271.917 18...  9.55706   
...          ...                                                ...      ...   
56075  E01033742  POLYGON ((544642.680 179824.674, 544766.313 17...   8.8281   
56088  E01033743  POLYGON ((546579.195 181097.813, 546687.036 18...  8.99324   
56101  E01033744  POLYGON ((544536.486 179447.115, 544602.630 17...  8.68114   
56114  E01033745  POLYGON ((546415.745 180152.270, 546320.715 18...  9.82933   
56127  E01033746  POLYGON ((538140.000 177313.000, 538129.177 17...  8.72132   

      saturate    sugar  protein     carb    fibre energy_tot  \
10     3.71757  9.44871    5.238   15.078  1.64311    166.494   
23     2.85281  8.29179  5.42597  13.6344  1.66645    147.436   
36     3.47299  9.64832  5.24885  15.8152  1.50681    166.045   
49     3.34494  9.56083  5.27735  17.3548  1.64318    170.011   
62     3.63843  11.1318  4.97023  20.4426  1.79831    192.011   
...        ...      ...      ...      ...      ...        ...   
56075  3.53288  9.10107  5.30437   16.965  1.56344    173.582   
56088  3.50634  10.2518   5.0883  19.6858  1.54783     184.03   
56101  3.23243  9.68737  5.33334  18.6313  1.51453    177.985   
56114  3.71612   10.086   5.1904  20.9763  1.70922     197.77   
56127  3.47482  9.26377  5.50625  18.0693  1.62906    177.358   

      h_nutrients_calories month agg_level  
10                 1.60131   Sep      lsoa  
23                 1.67933   Sep      lsoa  
36                 1.63671   Sep      lsoa  
49                 1.59396   Sep      lsoa  
62                 1.52385   Sep      lsoa  
...                    ...   ...       ...  
56075              1.59356   Sep      lsoa  
56088              1.53585   Sep      lsoa  
56101              1.55683   Sep      lsoa  
56114              1.53391   Sep      lsoa  
56127               1.5813   Sep      lsoa  

[4210 rows x 12 columns]

## Convert data into JSON format for Bokeh

In [76]:
import json
#Read data to json
def json_data(selectedMonth:str):
    mo = merged_tot[merged_tot['month'] == selectedMonth].query("agg_level=='lsoa'")
    merged_json = json.loads(mo.to_json())
    json_data = json.dumps(merged_json)
    return json_data

# Visualisation creation
## Set up

In [78]:
from bokeh.io import output_notebook, show, output_file
from bokeh.plotting import figure
from bokeh.models import GeoJSONDataSource, LinearColorMapper, ColorBar
from bokeh.palettes import brewer
from bokeh.io import curdoc, output_notebook
from bokeh.models import Slider, HoverTool
from bokeh.layouts import widgetbox, row, column

#Input GeoJSON source that contains features for plotting.
geosource = GeoJSONDataSource(geojson = json_data('Sep'))

## Color palette

In [79]:
#Define a sequential multi-hue color palette.
n_colors = 8
palette = brewer['YlGnBu'][n_colors]
#Reverse color order so that dark blue is highest obesity.
palette = palette[::-1]
#Instantiate LinearColorMapper that linearly maps numbers in a range, into a sequence of colors.
color_mapper = LinearColorMapper(
    palette = palette, nan_color='#d9d9d9',
    low = feature.min(), high = feature.max())
#Define custom tick labels for color bar.
tick_labels = {
    str(i):str(round(feature.min()+(feature.max()-feature.min())*i/n_colors,2)) 
    for i in range(n_colors+1)} 
#Create color bar. 
color_bar = ColorBar(
    color_mapper=color_mapper, label_standoff=n_colors,width = 500, height = 20,
    border_line_color=None,location = (0,0), orientation = 'horizontal', 
    major_label_overrides = tick_labels
   )

In [80]:
#Create figure object.
p = figure(
    title = 'Fibre consumption during period', 
    plot_height = 600 , plot_width = 950, toolbar_location = None)

In [81]:
# Define the callback function: update_plot
def update_plot(attr, old, new):
    mo = period[slider.value]
    new_data = json_data(mo)
    geosource.geojson = new_data
    p.title.text = 'Fibre consumption during period : ' + mo
# Make a slider object: slider 
period=['Apr', 'Aug', 'Dec', 'Feb', 'Jan', 'Jul', 'Jun', 'Mar', 'May',
       'Nov', 'Oct', 'Sep', 'yea']
slider = Slider(start=0, end=len(period)-1, value=0, step=1, title="Period")
slider.on_change('value', update_plot)

## Show map

In [82]:
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
p.axis.visible = False
#Add patch renderer to figure. 
p.patches('xs','ys', source = geosource,fill_color = {'field' :'fibre', 'transform' : color_mapper},
          line_color = 'black', line_width = 0.25, fill_alpha = 1)
p.add_layout(color_bar, 'below')
# Make a column layout of widgetbox(slider) and plot, and add it to the current document
layout = column(p,widgetbox(slider))
curdoc().add_root(layout)
#Display plot inline in Jupyter notebook
output_notebook()
#Display plot
show(layout)

Loading BokehJS ...

You are generating standalone HTML/JS output, but trying to use real Python
callbacks (i.e. with on_change or on_event). This combination cannot work.

Only JavaScript callbacks may be used with standalone output. For more
information on JavaScript callbacks with Bokeh, see:

    https://docs.bokeh.org/en/latest/docs/user_guide/interaction/callbacks.html

Alternatively, to use real Python callbacks, a Bokeh server application may
be used. For more information on building and running Bokeh applications, see:

    https://docs.bokeh.org/en/latest/docs/user_guide/server.html



In [83]:
p = figure(
    title = 'Pleutre', 
    plot_height = 600 , plot_width = 950, 
    toolbar_location = None)
    
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
p.axis.visible = False
#Add patch renderer to figure. 
p.patches('xs','ys', source = geosource, #====================================================================================================================================================================================================================================================================================================================
          fill_color = {'field' :'fibre', 'transform' : color_mapper},
          line_color = 'black', line_width = 0.25, fill_alpha = 1)
p.add_layout(color_bar, 'below')